In [32]:
# TFT MODEL

# ─────────────────────────────────────────────────────────────────────────
# DEPENDENCIAS INICIALES
# ─────────────────────────────────────────────────────────────────────────
from tqdm import tqdm
import os
import pickle
import pandas as pd
import numpy as np
from typing import Dict, Tuple, List

from darts import TimeSeries
from darts.models import TFTModel
from darts.metrics import smape
import optuna

# ─────────────────────────────────────────────────────────────────────────
# CONSTANTES Y RUTAS
# ─────────────────────────────────────────────────────────────────────────
BASE_PATH = "D:/lab3/Modelo_15"
DATASET_PATH = os.path.join(BASE_PATH, "dataset_nbeats_ready_robusto.csv")
SERIES_PKL = os.path.join(BASE_PATH, "series.pkl")
COVARS_PKL = os.path.join(BASE_PATH, "covars.pkl")
SERIES_FIL_PKL = os.path.join(BASE_PATH, "series_filtrado.pkl")
COVARS_FIL_PKL = os.path.join(BASE_PATH, "covars_filtrado.pkl")
TR_SERIES_PKL = os.path.join(BASE_PATH, "tr_series.pkl")
VAL_SERIES_PKL = os.path.join(BASE_PATH, "val_series.pkl")
TR_COV_PKL = os.path.join(BASE_PATH, "tr_cov.pkl")
VAL_COV_PKL = os.path.join(BASE_PATH, "val_cov.pkl")
BEST_PARAMS_PKL = os.path.join(BASE_PATH, "best_tft_params.pkl")
MODEL_PKL = os.path.join(BASE_PATH, "trained_tft_model.pkl")
PREDS_SCALED_PKL = os.path.join(BASE_PATH, "preds_scaled.pkl")
KAGGLE_CSV = os.path.join(BASE_PATH, "predicciones_kaggle.csv")

TRAIN_MONTHS = 30
PRED_HORIZON = 2
TOTAL_MONTHS = 36

# ─────────────────────────────────────────────────────────────────────────
# FUNCIONES
# ─────────────────────────────────────────────────────────────────────────

def load_dataset(path: str) -> pd.DataFrame:
    return pd.read_csv(path, parse_dates=["date"])

def create_series(df: pd.DataFrame) -> Tuple[Dict, Dict]:
    if os.path.exists(SERIES_PKL) and os.path.exists(COVARS_PKL):
        print("✔ series.pkl y covars.pkl encontrados, cargando...")
        return pickle.load(open(SERIES_PKL, "rb")), pickle.load(open(COVARS_PKL, "rb"))
    covar_cols = [c for c in df.columns if c not in ["product_id", "customer_id", "date", "tn", "tn_scaled"]]
    series, covars = {}, {}
    for (prod, cust), group in df.groupby(["product_id", "customer_id"]):
        group = group.sort_values("date")
        series[(prod, cust)] = TimeSeries.from_dataframe(group, "date", "tn_scaled")
        covars[(prod, cust)] = TimeSeries.from_dataframe(group, "date", covar_cols)
    pickle.dump(series, open(SERIES_PKL, "wb"))
    pickle.dump(covars, open(COVARS_PKL, "wb"))
    return series, covars

def split_series_and_save(series: Dict, covars: Dict):
    if all(os.path.exists(p) for p in [TR_SERIES_PKL, VAL_SERIES_PKL, TR_COV_PKL, VAL_COV_PKL]):
        print("✔ Splits ya generados, cargando...")
        return (
            pickle.load(open(TR_SERIES_PKL, "rb")),
            pickle.load(open(VAL_SERIES_PKL, "rb")),
            pickle.load(open(TR_COV_PKL, "rb")),
            pickle.load(open(VAL_COV_PKL, "rb"))
        )
    tr_series, val_series, tr_cov, val_cov = [], [], [], []
    for key in series:
        tr, val, tc, vc = split_series(series[key], covars[key])
        tr_series.append(tr)
        val_series.append(val)
        tr_cov.append(tc)
        val_cov.append(vc)
    pickle.dump(tr_series, open(TR_SERIES_PKL, "wb"))
    pickle.dump(val_series, open(VAL_SERIES_PKL, "wb"))
    pickle.dump(tr_cov, open(TR_COV_PKL, "wb"))
    pickle.dump(val_cov, open(VAL_COV_PKL, "wb"))
    return tr_series, val_series, tr_cov, val_cov

def split_series(ts, cov):
    return ts[:TRAIN_MONTHS], ts[TRAIN_MONTHS:], cov[:TRAIN_MONTHS], cov

def filter_invalid_splits(series: Dict, covars: Dict) -> Tuple[Dict, Dict]:
    if os.path.exists(SERIES_FIL_PKL) and os.path.exists(COVARS_FIL_PKL):
        print("✔ Series filtradas encontradas, cargando...")
        return pickle.load(open(SERIES_FIL_PKL, "rb")), pickle.load(open(COVARS_FIL_PKL, "rb"))
    valid_series, valid_covars = {}, {}
    for key, ts in series.items():
        tr, val = ts[:TRAIN_MONTHS], ts[TRAIN_MONTHS:]
        if np.all(tr.values() == 0) or np.all(val.values() == 0): continue
        if np.std(tr.values()) == 0 or np.std(val.values()) == 0: continue
        valid_series[key] = ts
        valid_covars[key] = covars[key]
    pickle.dump(valid_series, open(SERIES_FIL_PKL, "wb"))
    pickle.dump(valid_covars, open(COVARS_FIL_PKL, "wb"))
    return valid_series, valid_covars

import random
random.seed(42)

N_SAMPLE = 2_000 #numero deseries escogidas para Optuna de las 6700 aprox, aleatorias.
idx_sample = random.sample(range(len(tr_series)), N_SAMPLE)

tr_series_s  = [tr_series[i]  for i in idx_sample]
val_series_s = [val_series[i] for i in idx_sample]
tr_cov_s     = [tr_cov[i]     for i in idx_sample]
val_cov_s    = [val_cov[i]    for i in idx_sample]


def hyperparameter_search(tr_series, val_series, tr_cov, val_cov, n_trials=10) -> dict:
    if os.path.exists(BEST_PARAMS_PKL):
        print("✔ Hiperparámetros encontrados, cargando...")
        return pickle.load(open(BEST_PARAMS_PKL, "rb"))
    MAX_IN_CHUNK = TRAIN_MONTHS - PRED_HORIZON
    def objective(trial):
        params = {
            "input_chunk_length": trial.suggest_int("input_chunk_length", 12, MAX_IN_CHUNK),
            "output_chunk_length": PRED_HORIZON,
            "hidden_size": trial.suggest_categorical("hidden_size", [32, 64, 128]),
            "lstm_layers": trial.suggest_int("lstm_layers", 1, 3),
            "num_attention_heads": trial.suggest_categorical("num_attention_heads", [4, 8]),
            "dropout": trial.suggest_float("dropout", 0.0, 0.3),
            "batch_size": 64,
            "n_epochs": trial.suggest_int("n_epochs", 30, 80),
            "random_state": 42,
        }
        model = TFTModel(**params)
        model.fit(tr_series, future_covariates=tr_cov, verbose=False)
        preds = model.predict(n=len(val_series[0]), series=tr_series, future_covariates=val_cov)
        return np.mean([smape(v, p) for v, p in zip(val_series, preds)])
    study = optuna.create_study(direction="minimize")
    for _ in tqdm(range(n_trials), desc="🔍 Optuna search"):
       study.optimize(objective, n_trials=1, catch=(Exception,))
    pickle.dump(study.best_params, open(BEST_PARAMS_PKL, "wb"))
    return study.best_params

MODEL_PTH = os.path.join(BASE_PATH, "trained_tft_model.pth")

def train_final_model(series, covars, best_params):
    # cargar con método oficial (evita el bug)
    if os.path.exists(MODEL_PTH):
        print("✔ Modelo entrenado encontrado, cargando...")
        return TFTModel.load(MODEL_PTH)

    best_params.setdefault("input_chunk_length", 30)
    best_params.setdefault("output_chunk_length", 2)
    model = TFTModel(random_state=42, **best_params)
    model.fit(list(series.values()), future_covariates=list(covars.values()), verbose=True)

    model.save(MODEL_PTH)           # guarda con .save()
    return model

def extend_covariates(covariates_dict, n_months=2):
    """
    Devuelve un nuevo dict con las mismas covariables + meses 37-38
    conservando month, year, quarter, flags y dummies de estación.
    """
    extended = {}
    for key, ts in covariates_dict.items():
        df = pd.DataFrame(ts.values(), index=ts.time_index, columns=ts.columns)

        # fecha de corte y frecuencia
        last_date = df.index[-1]
        freq = df.index.freq or pd.infer_freq(df.index)

        # fechas futuras (n_months: 2 → meses 37-38)
        fut_dates = pd.date_range(start=last_date + pd.offsets.MonthBegin(),
                                  periods=n_months, freq=freq)

        fut = pd.DataFrame(index=fut_dates, columns=df.columns)

        # ── columnas calendario coherentes ─────────────────────────
        fut["month"]   = fut.index.month
        fut["year"]    = fut.index.year
        fut["quarter"] = fut.index.quarter
        fut["is_summer"]    = fut["month"].isin([12,1,2]).astype(int)
        fut["is_vacation"]  = fut["month"].isin([1,7,12]).astype(int)
        fut["is_peak_month"] = (fut["month"]==12).astype(int)

        def season(m): return ("summer","autumn","winter","spring")[(m%12)//3]
        fut["season"] = fut["month"].apply(season)

        for s in ["summer","autumn","winter","spring"]:
            col = f"season_{s}"
            fut[col] = (fut["season"] == s).astype(int)

        fut.drop(columns="season", inplace=True)

        # cualquier otra covariable, rellenar con 0
        fut.fillna(0, inplace=True)

        combined = pd.concat([df, fut])
        extended[key] = TimeSeries.from_dataframe(combined)

    return extended


def predict_next_two(model, series: Dict, covars: Dict) -> pd.DataFrame:
    if os.path.exists(PREDS_SCALED_PKL):
        print("✔ Predicciones ya generadas, cargando...")
        return pickle.load(open(PREDS_SCALED_PKL, "rb"))
    preds = []
    for (prod, cust), ts in series.items():
        cov = covars[(prod, cust)]
        pred = model.predict(n=PRED_HORIZON, series=ts, future_covariates=cov)
        preds.append({"product_id": prod, "customer_id": cust, "tn_scaled_pred": pred.values()[-1][0]})
    df_preds = pd.DataFrame(preds)
    pickle.dump(df_preds, open(PREDS_SCALED_PKL, "wb"))
    return df_preds

def prepare_kaggle_submission(preds_scaled: pd.DataFrame,
                              df_original: pd.DataFrame,
                              output_path: str):
    if os.path.exists(output_path):
        print("✔ Kaggle CSV ya existe.")
        return

    last_date = df_original["date"].max()

    # total real por producto en el último mes histórico
    prod_total = (
        df_original[df_original["date"] == last_date]
        .groupby("product_id")["tn"]
        .sum()
        .rename("tn_prod_total")
        .reset_index()
    )

    preds = preds_scaled.merge(prod_total, on="product_id", how="left")

    # des-escalar: ratio × total producto (NO por cliente)
    preds["tn_pred"] = preds["tn_scaled_pred"] * preds["tn_prod_total"]

    kaggle = (
        preds.groupby("product_id")["tn_pred"]
        .sum()
        .reset_index()
        .rename(columns={"tn_pred": "tn"})
    )

    kaggle.to_csv(output_path, index=False)
    print(f"CSV Kaggle guardado en {output_path}")



In [7]:
df = load_dataset(DATASET_PATH)
# 1. Carga el dataset original desde el CSV base

In [11]:
series_raw, covars_raw = create_series(df)
# 2. Genera las series y covariables (TimeSeries) para cada par producto-cliente

✔ series.pkl y covars.pkl encontrados, cargando...


In [12]:
pickle.dump(series_raw, open(SERIES_PKL, "wb"))
pickle.dump(covars_raw, open(COVARS_PKL, "wb"))
# 3. Guarda las series originales y covariables para evitar repetir

In [13]:
series, covars = filter_invalid_splits(series_raw, covars_raw)
# 4. Filtra series inválidas: constantes, vacías o con varianza cero

✔ Series filtradas encontradas, cargando...


In [14]:
pickle.dump(series, open(SERIES_FIL_PKL, "wb"))
pickle.dump(covars, open(COVARS_FIL_PKL, "wb"))
# 5. Guarda las versiones filtradas

In [15]:
tr_series, val_series, tr_cov, val_cov = split_series_and_save(series, covars)
# 6. Divide en train/valid en memoria las series filtradas (no guardadas)

✔ Splits ya generados, cargando...


In [16]:
N = 20
best_params = hyperparameter_search(tr_series[:N], val_series[:N], tr_cov[:N], val_cov[:N], n_trials=20)
# 7. Ejecuta Optuna sobre un subconjunto de N series para encontrar mejores hiperparámetros

✔ Hiperparámetros encontrados, cargando...


In [14]:
pickle.dump(best_params, open(BEST_PARAMS_PKL, "wb"))
# 8. Guarda los hiperparámetros óptimos

In [27]:
best_params["n_epochs"] = 3
model = train_final_model(series_raw, covars_raw, best_params)
# 9. Entrena el modelo final sobre todas las series crudas (`series_raw` y `covars_raw`)

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs

   | Name                              | Type                             | Params | Mode 
------------------------------------------------------------------------------------------------
0  | train_metrics                     | MetricCollection                 | 0      | train
1  | val_metrics                       | MetricCollection                 | 0      | train
2  | input_embeddings                  | _MultiEmbedding                  | 0      | train
3  | static_covariates_vsn             | _VariableSelectionNetwork        | 0      | train
4  | encoder_vsn                       | _VariableSelectionNetwork        | 40.5 K | train
5  | decoder_vsn                       | _VariableSelectionNetwork        | 37.0 K | train
6  | static_context_grn                | _GatedResidualNetwork            | 66.3 K | train
7  | static_context_hidden_encoder_grn | _GatedResidualNetwork 

Training: |          | 0/? [00:00<?, ?it/s]

`Trainer.fit` stopped: `max_epochs=3` reached.


In [28]:
covars_extended = extend_covariates(covars_raw, n_months=2)
# 10. Extiende las covariables a futuro para poder predecir M+1 y M+2

C:\Users\Charizard\AppData\Local\Temp\ipykernel_12600\761614146.py:181: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  fut.fillna(0, inplace=True)
C:\Users\Charizard\AppData\Local\Temp\ipykernel_12600\761614146.py:181: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  fut.fillna(0, inplace=True)
C:\Users\Charizard\AppData\Local\Temp\ipykernel_12600\761614146.py:181: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future 

In [29]:
preds_scaled = predict_next_two(model, series_raw, covars_extended)
# 11. Genera predicciones de tn_scaled para M+2

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs


...

Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

In [30]:
prepare_kaggle_submission(preds_scaled, df, KAGGLE_CSV)
# 12. Desescala tn y genera el archivo final para Kaggle (por producto)

CSV Kaggle guardado en D:/lab3/Modelo_15\predicciones_kaggle.csv
